In [1]:
import os, argparse
from build_nnfps import main as build_nnfps_main
import numpy as np
import pandas as pds
import pickle, math
from preprocessing import data_preparation, _char_set, get_property, canonocalize
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_absolute_error
import SSVAE
import torch

# Molecule fingerprint regeneration for transfer learning, if necessary

In [2]:
# training datafiles to use, pick the combination as you like
csv_files = ['./data/paper_MP_IE_EA.csv',
             './data/paper_MP_clean_canonize_cut.csv',
             './data/paper_ZINC_310k.csv',
             './data/paper_clean_viscosity.csv',
             './data/paper_pubchem_fluorocarbon.csv'] 
# 'data/paper_clean_DC.csv' is skipped for now because it has many wrong & unphysical labels because of NLP

out_pkl = 'data/smiles2nn.pkl'
if os.path.isfile(out_pkl):
    os.system('rm '+out_pkl)

first = True
for csv_file in csv_files:
    args = argparse.Namespace()
    args.csv_file = csv_file
    if first:
        args.input_vocab_file = ''
        args.output_vocab_file = out_pkl
        args.fp_check = False
        # build_nnfps_main(args)
        first = False
    else:
        args.input_vocab_file = out_pkl
        args.output_vocab_file = out_pkl
        args.fp_check = False
        # build_nnfps_main(args)

# Prepare Combination of Dirty Data for Training SSVAE Model

In [3]:
# are we doing pre-training version? if yes, change pretrain to True
pretrain = False
pretrain_pkl = 'data/smiles2nn.pkl'

# we will try train generative model with these training data files
if 'csv_files' in locals():
    data_uri = csv_files
else:
    data_uri = ['./data/paper_MP_IE_EA.csv',
                './data/paper_MP_clean_canonize_cut.csv',
                './data/paper_ZINC_310k.csv',
                './data/paper_clean_viscosity.csv',
                './data/paper_pubchem_fluorocarbon.csv'] 

# first check how many data points we have in the training data
tmp_smiles = {}
for csv_in in data_uri:
    data = pds.read_csv( csv_in )
    for i in range(len(data['SMILES'])):
        tmp_smiles[ canonocalize(data['SMILES'][i]) ] = True

# define training, validation, and test set division
ntotal = len(tmp_smiles)
ntrn = math.floor( 0.9 * ntotal )
ntst = ntotal - ntrn
frac_val = 0.05
del data, tmp_smiles

# data preparation
if pretrain:
    data, scaler_Y = data_preparation(data_uri, ntrn, ntst,
                                      frac_val = frac_val,
                                      pretrain_uri = pretrain_pkl)
else:
    data, scaler_Y = data_preparation(data_uri, ntrn, ntst,
                                      frac_val = frac_val)

# tag for dumping intermediate models
dt = '221122121322'
model_dir = 'models/'+dt
tmp_model_tag = model_dir+'/'    
scaler_Y_pkl = 'preprocessed_scaler_Y.pkl'
scaler_Y = pickle.load(open(tmp_model_tag+scaler_Y_pkl,'rb'))

print('::: Data preparation completed')

::: Data preparation completed


# Load Previously Trained Model, if Needed

In [4]:
# pre-defined parameters
beta=10000.
char_set = _char_set()
dim_z = 100
dim_h = 250
n_hidden = 3
batch_size = 100

# tag for dumping intermediate models
save_uri = tmp_model_tag+'model_final.pth.tar'

# Instantiate the model
model = SSVAE.TorchModel(sample_data = data, dim_z = dim_z, dim_h = dim_h,
                         n_hidden = n_hidden, batch_size = batch_size, beta = float(beta), char_set = char_set,
                         tmp_model_tag = tmp_model_tag)
dev = torch.device('cuda:0') if torch.cuda.is_available() else torch.device('cpu')
model.initialize(torch.Tensor(data['trnY']), torch.Tensor(data['trnMask']), dev)
model.load_state_dict( torch.load(save_uri)['state_dict'] )
model.eval()

TorchModel(
  (predictor): bi_GRU_zero(
    (GRU): GRU(43, 250, num_layers=3, batch_first=True, bidirectional=True)
    (linear_out_y): Linear(in_features=500, out_features=12, bias=True)
  )
  (encoder): bi_GRU_init(
    (GRU): GRU(86, 250, num_layers=3, batch_first=True, bidirectional=True)
    (linear_in): Linear(in_features=6, out_features=500, bias=True)
    (linear_peek): Linear(in_features=6, out_features=43, bias=True)
    (linear_out_z): Linear(in_features=500, out_features=200, bias=True)
  )
  (decoder): uni_GRU_init(
    (GRU): GRU(86, 250, num_layers=3, batch_first=True)
    (linear_in): Linear(in_features=106, out_features=250, bias=True)
    (linear_peek): Linear(in_features=106, out_features=43, bias=True)
    (linear_out_x): Linear(in_features=250, out_features=43, bias=True)
  )
  (softmax): Softmax(dim=-1)
  (sigmoid): Sigmoid()
)

# Property Prediction Performance

In [5]:
scaled_tstY_hat = model.predict_routine(sample_data = data).detach().cpu().numpy()
tstY_hat = [scaler_Y[i].inverse_transform(scaled_tstY_hat[:,i:i+1]) for i in range(scaled_tstY_hat.shape[1])]
tstY_hat = np.concatenate(tstY_hat, axis=1)

dim_y = data['dim_y']
tstY = data['tstY']
tstMask = data['tstMask']
Y_names = data['Y_names']
for j in range(dim_y):
    idx = np.where( tstMask[:,j] == 1 )[0]
    print('Label Name:', Y_names[j])
    print([j, mean_absolute_error(tstY[idx,j], tstY_hat[idx,j])])

Label Name: EA
[0, 0.13637408803535833]
Label Name: IE
[1, 0.14150882359853362]
Label Name: LogVis
[2, 0.11567929813698415]
Label Name: MolWt
[3, 1.4402104748643125]
Label Name: n_F
[4, 0.012866710001588365]
Label Name: n_O
[5, 0.020168003558247206]


# Unconditional Generation

In [6]:
print('Unconditional')
for t in range(10):
    smi = model.sampling_unconditional()
    print([t, smi, get_property(smi)])

Unconditional
[0, 'NC(=S)c1cccc(NC(=O)c2ccc(C(F)(F)F)cc2Cl)c1', [358.01544628, 4.245300000000001, 0.8065823973953891]]
[1, 'CC(Oc1ccc2c(c1)OCO2)C(=O)OC(C)(C)F', [270.0903518, 2.4314, 0.786409830011752]]
[2, 'CCOC(=O)c1sc(-c2ccc(C(F)(F)F)cc2Cl)nc1C(F)F', [384.996268308, 5.596600000000003, 0.5079500393681798]]
[3, 'O=C(C1CCCN(c2nc3ccccc3s2)C(=O)N1)N1CCN(Cc2ccc(Cl)cc2)CC1', [483.14957375200004, 3.972500000000003, 0.6092607553458744]]
[4, 'O=C(Oc1ccncc1Cl)c1ccc(F)cc1F', [269.00551255199997, 3.232400000000001, 0.7858965839289802]]
[5, 'Cc1c(Br)cc(Br)cc1S(=O)(=O)Nc1ccc(OC(F)(F)F)cc1', [486.8700230399999, 5.219420000000001, 0.6414968283828476]]
[6, 'NC(c1ccc(C(F)(F)F)cc1)C(F)(F)C(F)F', [275.05449679599997, 3.605600000000001, 0.837821647001269]]
[7, 'CN1N=C(c2ccc(F)cc2)C(=O)C1=Cc1ccc(Oc2ccc(F)cc2)cc1', [390.117984192, 5.0168000000000035, 0.5878703316386003]]
[8, 'C#CC(C)(O)c1ccc(Cl)cc1', [180.034192588, 2.1807, 0.6572933820183905]]
[9, 'C=CCN1C(=O)C(=Cc2ccc(OCc3ccc(F)cc3)cc2)C(=O)NC1=S', [396.

# Conditional Generation

In [7]:
print('Conditional')
# Determine the property values we want to use for conditional generation
ynames = ['EA', 'IE', 'LogVis', 'MolWt', 'n_F', 'n_O']
yids = [Y_names.index(yname) for yname in ynames]

for i1 in [0.5, 0.0]:
    for i2 in [7.0, 7.5]:
        for i3 in [0.0, -0.1]:
            for i4 in [250, 300]:
                for i5 in [4.0, 6.0]:
                    for i6 in [1.0, 2.0]:
                        ytargets = [i1,i2,i3,i4,i5,i6]
                        ymeans = np.array([scaler_Y[yid].mean_[0] for yid in yids])
                        ystds = np.array([np.sqrt(scaler_Y[yid].var_[0]) for yid in yids])
                        ytargets_transform = ( np.array(ytargets) - ymeans ) / ystds
                        
                        print(ynames, ':', ytargets)
                        for t in range(1000):
                            smi = model.sampling_conditional(yids, ytargets_transform)
                            print([t, smi, get_property(smi)])
                        print('')

Conditional
['EA', 'IE', 'LogVis', 'MolWt', 'n_F', 'n_O'] : [0.5, 7.0, 0.0, 250, 4.0, 1.0]


RDKit ERROR: [15:22:02] Can't kekulize mol.  Unkekulized atoms: 1 2 3 4 15
[15:22:02] Can't kekulize mol.  Unkekulized atoms: 1 2 3 4 15

RDKit ERROR: 


[0, 'Cc1ccc(OC(F)(F)c2ccccc2)c1F', 'invalid']
[1, 'COc1cc(F)c(C(F)(F)F)c(CC#N)c1C', [247.062026788, 3.2276000000000016, 0.7514830846941175]]
[2, 'OC(Cc1cc(F)cc(Cl)c1)C(F)(F)F', [242.012155404, 2.9448000000000008, 0.790876585792075]]
[3, 'CCc1c(OC(F)(F)F)ccc(C#N)c1CF', [247.062026788, 3.488780000000001, 0.7657581490906114]]
[4, 'FC(F)(F)Oc1ccnc(-c2ccccc2)c1F', [257.046376724, 3.7863000000000016, 0.7635081948672656]]
[5, 'Cn1c(C(F)(F)F)cc(=O)c2cc(F)ccc21', [245.046376724, 2.6964000000000006, 0.6539029959969263]]
[6, 'COc1ccc(NCC(F)(F)C(F)F)cc1C', [251.093326916, 3.315920000000001, 0.8104424486495876]]
[7, 'Cc1cc(OC(F)(F)F)c(F)cc1CCl', [242.012155404, 3.7715200000000015, 0.566594699206567]]
[8, 'Cc1cn(-c2cc(F)c(F)c(F)c2F)c(=O)[nH]1', [246.041625692, 2.03042, 0.4663566114562579]]
[9, 'Cn1ccc(C(=O)NCC(F)(F)C(F)(F)F)n1', [257.058752976, 1.3475, 0.8306493052086789]]
[10, 'CC(NC(=O)C(F)(F)C(F)F)c1ccccn1', [250.07292582, 2.1592000000000002, 0.8318563893316389]]
[11, 'N[C@@H](CC(=O)Nc1cc(F)ccc1F

RDKit ERROR: [15:25:39] SMILES Parse Error: unclosed ring for input: 'Cn1c(C(F)(F)F)cc(=O)c2ccc(F)cc2c12'
[15:25:39] SMILES Parse Error: unclosed ring for input: 'Cn1c(C(F)(F)F)cc(=O)c2ccc(F)cc2c12'


[75, 'Cn1c(C(F)(F)F)cc(=O)c2ccc(F)cc2c12', 'invalid']
[76, 'COc1ccc(C(F)(F)C(F)(F)Cl)cc1', [242.012155404, 3.6186000000000016, 0.5810727648261791]]
[77, 'NCCC(=O)Nc1ccc(F)c(C(F)(F)F)c1', [250.07292582, 2.1318, 0.8072665330370883]]
[78, 'OCc1cc(C(F)(F)F)c(F)cc1CCl', [242.012155404, 3.0756000000000006, 0.6242110973374227]]
[79, 'FC(F)(F)CCCOc1c(F)cccc1Cl', [256.027805468, 4.200400000000002, 0.5794309881817146]]
[80, 'Cc1cc(F)c(-c2noc(C(F)(F)F)n2)cc1', [246.041625692, 3.2029200000000007, 0.7250449101025541]]
[81, 'O=Cc1cc(F)cc(-c2cc(F)c(F)c(F)c2)c1', [254.035477692, 3.722500000000001, 0.4531818304446574]]
[82, 'CN(CC(F)(F)F)C(=O)c1ccc(F)cc1C', [249.077676852, 2.7684200000000008, 0.7378856227576113]]
[83, 'COc1ncc(Cl)cc1C(F)(F)C(F)F', [243.007404372, 3.100500000000001, 0.7613124133239076]]
[84, 'OCc1cc(C(F)(F)F)ccc1SC(F)F', [258.013776944, 3.5124000000000013, 0.6609483917482573]]
[85, 'CC(=O)Nc1cc(C(F)(F)F)c(F)cc1CN', [250.07292582, 2.2615999999999996, 0.790863215813087]]
[86, 'Oc1c(F)cc(-

...

RDKit ERROR: [00:27:20] Can't kekulize mol.  Unkekulized atoms: 2 3 4 5 6
[00:27:20] Can't kekulize mol.  Unkekulized atoms: 2 3 4 5 6

RDKit ERROR: 


[867, 'O=c1cccnc1COCC(F)(F)C(F)C(F)C(F)F', 'invalid']
[868, 'NC(=O)c1c(C(F)(F)F)cnc(OCC(F)(F)F)c1C', [302.048996816, 2.4488200000000004, 0.8722172921228635]]
[869, 'Cc1cccc(CC(O)(C(F)(F)F)C(F)(F)F)c1CO', [302.074148944, 2.885520000000002, 0.8429654100848992]]
[870, 'FC(F)(F)OCCOc1ccc(C(F)(F)F)c(Cl)c1', [308.00387646400003, 4.274000000000002, 0.6105606940536087]]
[871, 'OC(CCC(F)(F)C(F)(F)C(F)F)c1ccc(O)cc1', [302.074148944, 3.741500000000002, 0.785887824370463]]
[872, 'O=C(Nc1ccc(OCC(F)(F)F)cc1)CC(F)(F)F', [301.05374784800006, 3.518600000000001, 0.8641687351146128]]
[873, 'O=C(NCC(F)(F)F)c1ccc(OCC(F)(F)F)cc1', [301.05374784800006, 2.9198000000000013, 0.8684401372742389]]
[874, 'CC(C)(C)OC(=O)NCC(C(F)(F)F)CC(F)(F)F', [295.10069804000005, 3.642000000000002, 0.8072110648443729]]
[875, 'CCOCc1c(OC(F)(F)F)cc(C(F)(F)F)nc1C', [303.06939791200006, 3.8439200000000016, 0.7918818788605614]]
[876, 'Oc1c(OC(F)(F)F)cc(C(F)(F)F)nc1CCl', [294.983475368, 3.4433999999999996, 0.6710979848695784]]
[877, 'C

RDKit ERROR: [00:34:05] Can't kekulize mol.  Unkekulized atoms: 1 2 4 6 18
[00:34:05] Can't kekulize mol.  Unkekulized atoms: 1 2 4 6 18

RDKit ERROR: 


[981, 'Fc1c(F)c(F)c(-c2ccc(OC(F)(F)F)cc2)c1O', 'invalid']
[982, 'Oc1nc(OC(F)(F)F)cc(C(F)(F)F)c1CCl', [294.983475368, 3.4433999999999996, 0.6710979848695784]]
[983, 'NC(=O)c1cccc(COC(C(F)(F)F)C(F)(F)F)c1', [301.05374784800006, 2.795300000000001, 0.8694427292136977]]
[984, 'OCc1c(C(F)(F)F)cnc(OC(F)(F)F)c1C1CC1', [301.05374784800006, 3.3687000000000014, 0.8704285529946028]]
[985, 'OCCc1nc(CC(F)(F)F)ccc1OC(F)(F)F', [289.05374784800006, 2.6198000000000006, 0.866387742501843]]
[986, 'OC(O)c1c(C(F)(F)F)ccc(Cl)c1C(F)(F)F', [293.98822640000003, 3.3607999999999993, 0.6157475471025697]]
[987, 'CCOC(=O)c1ccc(C(F)(F)C(F)(F)C(F)F)cc1', [300.05849888, 3.855500000000002, 0.6095558975442841]]
[988, 'OCC(Oc1cc(C(F)(F)F)cc(C(F)(F)F)c1)CC', [302.074148944, 3.8739000000000017, 0.8554780655624893]]
[989, 'COc1ccc(C(F)(F)C(F)(F)C(F)(F)CO)s1', [294.014919816, 3.111400000000001, 0.8455530141355533]]
[990, 'COCCc1c(OC(F)(F)F)ncc(C(F)(F)F)c1C', [303.06939791200006, 3.4963200000000025, 0.7978589313869222]]
[991, 

RDKit ERROR: [00:35:11] SMILES Parse Error: extra open parentheses for input: 'O=S(=O)(c1cc(C(F)(F)F)c(C(F)(F)F)cs1'
[00:35:11] SMILES Parse Error: extra open parentheses for input: 'O=S(=O)(c1cc(C(F)(F)F)c(C(F)(F)F)cs1'
